# Software Development Tools Sprint Project EDA

This project is to perform an analysis for a vehicle sale advertisement website to find which factors affecting the price of a vehicle. Hundreds of free advertisements for vechicles are published on the website everyday, this project will analyse the data collected over the last few years and determine which factors have impacts on the price of a vehicle.

In [1]:
# Importing necessary libraries
import pandas as pd
import plotly.express as px

## Importing website data

Here we add the data into a DataFrame and display the info and a sample of the data.

In [2]:
# Importing the data into a pandas DataFrame
try:
    df = pd.read_csv('vehicles_us.csv')
except:
    df = pd.read_csv('/SDT_Project/vehicles_us.csv')
# Reading data from the table
df.info()
df

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


price  model_year           model  condition  cylinders fuel  odometer  \
0       9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1      25500         NaN      ford f-150       good        6.0  gas   88705.0   
2       5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3       1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4      14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   
...      ...         ...             ...        ...        ...  ...       ...   
51520   9249      2013.0   nissan maxima   like new        6.0  gas   88136.0   
51521   2700      2002.0     honda civic    salvage        4.0  gas  181500.0   
51522   3950      2009.0  hyundai sonata  excellent        4.0  gas  128000.0   
51523   7455      2013.0  toyota corolla       good        4.0  gas  139573.0   
51524   6300      2014.0   nissan altima       good        4.0  gas       NaN   

      transmission    type paint_color  is_4wd date_posted  days_listed  
0        automatic     SUV         NaN     1.0  2018-06-23           19  
1        automatic  pickup       white     1.0  2018-10-19           50  
2        automatic   sedan         red     NaN  2019-02-07           79  
3        automatic  pickup         NaN     NaN  2019-03-22            9  
4        automatic   sedan       black     NaN  2019-04-02           28  
...            ...     ...         ...     ...         ...          ...  
51520    automatic   sedan       black     NaN  2018-10-03           37  
51521    automatic   sedan       white     NaN  2018-11-14           22  
51522    automatic   sedan        blue     NaN  2018-11-15           32  
51523    automatic   sedan       black     NaN  2018-07-02           71  
51524    automatic   sedan         NaN     NaN  2018-06-05           10  

[51525 rows x 13 columns]

There are 51525 vehicles and 13 columns of relevant data

**According to the documentation:**
- `price` = price of the vehicle
- `model_year` = model year of the vehicle
- `model` = model of the vehicle
- `condition` = condition of the vehicle (excellent, good, fair, etc.)
- `cylinders` = number of cylinders in the vehicle engine
- `fuel` = type of fuel the vehicle takes (gas, diesel, etc.)
- `odometer` = the mileage of the vehicle when it was published to the website
- `transmission` = automatic, manual, other
- `paint_color` = color of the vehicle
- `is_4wd` = if the vehicle has 4-wheel drive (Boolean)
- `date_posted` = the date the vehicle was published to the site
- `days_listed` = how long the vehicle was on the site to removal

**Now we look at some statistics and make a few initial observations:**

In [3]:
display(df.describe(include=['object']))
df.describe()

model  condition   fuel transmission   type paint_color  \
count        51525      51525  51525        51525  51525       42258   
unique         100          6      5            3     13          12   
top     ford f-150  excellent    gas    automatic    SUV       white   
freq          2796      24773  47288        46902  12405       10029   

       date_posted  
count        51525  
unique         354  
top     2019-03-17  
freq           186

price    model_year     cylinders       odometer   is_4wd  \
count   51525.000000  47906.000000  46265.000000   43633.000000  25572.0   
mean    12132.464920   2009.750470      6.125235  115553.461738      1.0   
std     10040.803015      6.282065      1.660360   65094.611341      0.0   
min         1.000000   1908.000000      3.000000       0.000000      1.0   
25%      5000.000000   2006.000000      4.000000   70000.000000      1.0   
50%      9000.000000   2011.000000      6.000000  113000.000000      1.0   
75%     16839.000000   2014.000000      8.000000  155000.000000      1.0   
max    375000.000000   2019.000000     12.000000  990000.000000      1.0   

       days_listed  
count  51525.00000  
mean      39.55476  
std       28.20427  
min        0.00000  
25%       19.00000  
50%       33.00000  
75%       53.00000  
max      271.00000

We can see the `price` and `model_year` have unusually low minimum values, an issue we will explore later. 

`is_4wd` is a boolean column and can be cleaned easily, then we will group the data to fill the other missing data. 

## Checking for duplicate and/or missing data

We will now check the DataFrame for duplicate entries and explore the columns that contain null values in order to determine if we will need to use any default values.

### Duplicate data

In [4]:
df.duplicated().sum()

0

The table does not include any unique id value for the vehicles so we look for duplicates across the whole DataFrame. None are found, so no further action is required.

### Missing Data

In [5]:
df.isna().sum()

price               0
model_year       3619
model               0
condition           0
cylinders        5260
fuel                0
odometer         7892
transmission        0
type                0
paint_color      9267
is_4wd          25953
date_posted         0
days_listed         0
dtype: int64

The only columns with missing values are the `model_year`, `cylinders`, `odometer`, `paint_color` and `is_4wd` columns. 

We will address the `is_4wd` boolean column first, then look at a few statistics to determine how to best fill the other missing values.

#### `is_4wd`

In [6]:
df['is_4wd'].value_counts(dropna=False)

is_4wd
NaN    25953
1.0    25572
Name: count, dtype: int64

Because this is a boolean column, we can replace all missing values with 0 to represent **False.** Data type will also be converted to `int`.

In [7]:
df['is_4wd'] = df['is_4wd'].fillna(0).astype('int')
df['is_4wd'].value_counts()

is_4wd
0    25953
1    25572
Name: count, dtype: int64

In [8]:
df.isna().sum()

price              0
model_year      3619
model              0
condition          0
cylinders       5260
fuel               0
odometer        7892
transmission       0
type               0
paint_color     9267
is_4wd             0
date_posted        0
days_listed        0
dtype: int64

***
#### `cylinders`

In [9]:
display(df['cylinders'].value_counts(dropna=False))

cylinders
8.0     15844
6.0     15700
4.0     13864
NaN      5260
10.0      549
5.0       272
3.0        34
12.0        2
Name: count, dtype: int64

We can see that 5260 cells are missing, and that most vehicles have $8$, $6$ or $4$ cylinders.

However, other factors like `model` and `transmission` could influence which average we should replace the missing values with:

In [10]:
cylinders = df.groupby(['model', 'transmission'])['cylinders'].value_counts(dropna=False).to_frame()
display(cylinders.head(25))
cylinders = df.groupby('model')['cylinders'].value_counts(dropna=False).to_frame()
print('-'*100)
cylinders.head(25)

count
model             transmission cylinders       
acura tl          automatic    6.0          200
                               NaN           25
                               4.0            3
                  manual       6.0            8
bmw x5            automatic    6.0          196
                               8.0           48
                               NaN           16
                  manual       6.0            3
                               8.0            3
                  other        6.0            1
buick enclave     automatic    6.0          243
                               NaN           24
                               8.0            1
                               4.0            1
                  manual       6.0            2
cadillac escalade automatic    8.0          289
                               NaN           27
                               6.0            2
                  manual       NaN            1
                               6.0            1
                  other        10.0           1
                               8.0            1
chevrolet camaro  automatic    6.0          188
                               8.0           57
                               NaN           30

----------------------------------------------------------------------------------------------------


count
model                        cylinders       
acura tl                     6.0          208
                             NaN           25
                             4.0            3
bmw x5                       6.0          200
                             8.0           51
                             NaN           16
buick enclave                6.0          245
                             NaN           24
                             8.0            1
                             4.0            1
cadillac escalade            8.0          290
                             NaN           28
                             6.0            3
                             10.0           1
chevrolet camaro             6.0          223
                             8.0          106
                             NaN           42
                             10.0          34
                             4.0            9
chevrolet camaro lt coupe 2d 6.0          281
                             NaN           30
chevrolet colorado           6.0          101
                             5.0           82
                             4.0           79
                             NaN           22

We see that `model` and `transmission` both do influence the amount of `cylinders` however we will use the mode for `model` only as including `transmission` does not affect the mode enough and more often reinforces the number of cylinders. The column will also be converted to the `int` data type.

In [11]:
df.loc[df['cylinders'].isna(), 'cylinders'] = (
    df.groupby('model')['cylinders'].transform(lambda cylinders: cylinders.mode().iloc[0])
)
df['cylinders'] = df['cylinders'].astype('int')
df['cylinders'].value_counts()

cylinders
8     17712
6     17457
4     15499
10      549
5       272
3        34
12        2
Name: count, dtype: int64

In [12]:
df.isna().sum()

price              0
model_year      3619
model              0
condition          0
cylinders          0
fuel               0
odometer        7892
transmission       0
type               0
paint_color     9267
is_4wd             0
date_posted        0
days_listed        0
dtype: int64

***
#### `model_year`

In [13]:
df['model_year'].value_counts(dropna=False).sort_index()

model_year
1908.0       2
1929.0       1
1936.0       1
1948.0       1
1949.0       1
          ... 
2016.0    2954
2017.0    2419
2018.0    2193
2019.0     380
NaN       3619
Name: count, Length: 69, dtype: int64

We can see 3619 cells are missing values and that there are 69 total unique `model_year` values. 

We can see quite a few outlier values under 1960:

In [14]:
model_year_fig = px.box(df, x='model_year', title='Boxplot of model year')
model_year_fig.show()

In [15]:
df.query('model_year <= 1960')

price  model_year               model  condition  cylinders fuel  \
10018  23900      1955.0           ford f250  excellent          6  gas   
14752  15000      1954.0          ford f-150  excellent          8  gas   
22595  21000      1948.0    chevrolet impala   like new          8  gas   
28009  65000      1960.0  chevrolet corvette   like new          8  gas   
33007  17500      1960.0    chevrolet impala  excellent          8  gas   
33906  12995      1908.0           gmc yukon       good          8  gas   
33907  12995      1908.0   cadillac escalade  excellent          8  gas   
34713   5000      1936.0          ford f-150  excellent          6  gas   
36582  44900      1949.0  chevrolet suburban       good          8  gas   
39580  35000      1958.0    chevrolet impala  excellent          8  gas   
40089  20000      1960.0    chevrolet impala  excellent          8  gas   
45694  18000      1929.0          ford f-150       good          8  gas   
48414  37900      1958.0    chevrolet impala       good          8  gas   

       odometer transmission    type paint_color  is_4wd date_posted  \
10018   47180.0       manual   truck        blue       0  2018-12-22   
14752    3565.0       manual  pickup       black       0  2019-02-16   
22595    4000.0    automatic   sedan         red       0  2019-01-18   
28009       NaN       manual   coupe         NaN       0  2018-11-03   
33007   31000.0    automatic   sedan       white       0  2019-02-01   
33906  169328.0    automatic     SUV       black       0  2018-07-06   
33907       NaN    automatic     SUV       white       0  2018-06-24   
34713   30000.0       manual  pickup      purple       0  2018-11-22   
36582    1800.0    automatic   wagon      orange       0  2018-08-19   
39580    3184.0    automatic   coupe       black       0  2018-05-19   
40089    1000.0    automatic   sedan      custom       0  2018-06-30   
45694       NaN       manual   other      silver       0  2018-11-18   
48414   62799.0    automatic   coupe         NaN       0  2018-08-11   

       days_listed  
10018           61  
14752           13  
22595           24  
28009           41  
33007           11  
33906           34  
33907           25  
34713           10  
36582           10  
39580           33  
40089           75  
45694           59  
48414           10

After looking on the internet we are able to determine that the `model_year` for these vehicles cannot be accurate:

- [ford f250](https://cars.com/research/ford-f_250/) Released in 1997
- [ford f-150](https://www.cars.com/research/ford-f_150/) Released in 1948
- [chevrolet impala](https://www.cars.com/research/chevrolet-impala/) Released in 1958
- [chevrolet corvette](https://cars.com/research/chevrolet-corvette/) Released in 1953
- [gmc yukon](https://cars.com/research/gmc-yukon/) Released in 1992
- [cadillac escalade](https://cars.com/research/cadillac-escalade/) Released in 1999

In [16]:
incorrect_model_year = [10018, 22595, 33906, 33907, 34713, 45694]
avg_model_year = df.groupby('model')['model_year'].agg('median').to_frame()

df.loc[incorrect_model_year, 'model_year'] = (
    df.groupby('model')['model_year'].transform(lambda model_year : model_year.mode().iloc[0]).astype('int')
)
df[df.index.isin(incorrect_model_year)]

price  model_year              model  condition  cylinders fuel  \
10018  23900      2008.0          ford f250  excellent          6  gas   
22595  21000      2008.0   chevrolet impala   like new          8  gas   
33906  12995      2007.0          gmc yukon       good          8  gas   
33907  12995      2007.0  cadillac escalade  excellent          8  gas   
34713   5000      2013.0         ford f-150  excellent          6  gas   
45694  18000      2013.0         ford f-150       good          8  gas   

       odometer transmission    type paint_color  is_4wd date_posted  \
10018   47180.0       manual   truck        blue       0  2018-12-22   
22595    4000.0    automatic   sedan         red       0  2019-01-18   
33906  169328.0    automatic     SUV       black       0  2018-07-06   
33907       NaN    automatic     SUV       white       0  2018-06-24   
34713   30000.0       manual  pickup      purple       0  2018-11-22   
45694       NaN       manual   other      silver       0  2018-11-18   

       days_listed  
10018           61  
22595           24  
33906           34  
33907           25  
34713           10  
45694           59

Here we can see that all the incorrect model years have been replaced by the average value for that model.

Now we use the same method to fill in missing values, and then we will convert the data type to `int`.

In [17]:
df.loc[df['model_year'].isna(), 'model_year'] = (
    df.groupby('model')['model_year'].transform(lambda model_year : model_year.mode().iloc[0]).astype('int')
)
df['model_year'] = df['model_year'].astype('int')
df['model_year'].value_counts(dropna=False).sort_index()

model_year
1949       1
1954       1
1958       2
1960       3
1961       1
        ... 
2015    3761
2016    3141
2017    2526
2018    2259
2019     380
Name: count, Length: 63, dtype: int64

In [18]:
df.isna().sum()

price              0
model_year         0
model              0
condition          0
cylinders          0
fuel               0
odometer        7892
transmission       0
type               0
paint_color     9267
is_4wd             0
date_posted        0
days_listed        0
dtype: int64

***
#### `odometer`

In [19]:
df['odometer'].value_counts(dropna=False)

odometer
NaN         7892
0.0          185
140000.0     183
120000.0     179
130000.0     178
            ... 
87836.0        1
172625.0       1
103597.0       1
167239.0       1
139573.0       1
Name: count, Length: 17763, dtype: int64

We can see 7892 cells with missing values. We will look at a few other columns to determine the best way to fill the missing values.

In [20]:
odometer = df.groupby('model')['odometer'].agg('median').to_frame()
px.bar(odometer, title='Odometer grouped by model').show()
odometer = df.groupby('condition')['odometer'].agg('median').sort_values().to_frame()
print('-'*100)
px.bar(odometer, title='Odometer grouped by condition').show()
odometer = df.groupby('model_year')['odometer'].agg('median').to_frame()
print('-'*100)
px.bar(odometer, title='Odometer grouped by model_year').show()

----------------------------------------------------------------------------------------------------


----------------------------------------------------------------------------------------------------


We can see from these visualizations that `condition` and `model_year` both have influence on `odometer` readings, however it looks like `condition` has much more influence, so we will use that to fill our missing values.

In [21]:
df['odometer'] = df[['odometer', 'condition']].groupby('condition').transform(lambda x:x.fillna(x.median()))
df['odometer'].value_counts(dropna=False)

odometer
104230.0    3803
129000.0    3199
72982.5      728
181613.0     237
0.0          185
            ... 
206213.0       1
69150.0        1
109925.0       1
214175.0       1
139573.0       1
Name: count, Length: 17765, dtype: int64

In [22]:
df.isna().sum()

price              0
model_year         0
model              0
condition          0
cylinders          0
fuel               0
odometer           0
transmission       0
type               0
paint_color     9267
is_4wd             0
date_posted        0
days_listed        0
dtype: int64

***
#### `paint_color`

In [23]:
# Check for missing values
df['paint_color'].value_counts(dropna=False)

paint_color
white     10029
NaN        9267
black      7692
silver     6244
grey       5037
blue       4475
red        4421
green      1396
brown      1223
custom     1153
yellow      255
orange      231
purple      102
Name: count, dtype: int64

We can see there are $9267$ missing values, with most vehicles having a greyscale color:
- white
- black
- silver
- grey

However, rather than use the overall most common we will use a similar method to the `cylinders` column, grouping by model and using that average.

In [24]:
# Check to see the paint_color based on model
df.groupby('model')['paint_color'].value_counts(dropna=False).to_frame().head(50)

count
model             paint_color       
acura tl          grey            55
                  NaN             48
                  black           44
                  silver          36
                  white           26
                  blue             9
                  green            7
                  red              5
                  yellow           2
                  brown            2
                  custom           2
bmw x5            black           66
                  NaN             58
                  grey            42
                  white           38
                  silver          32
                  blue            16
                  brown            6
                  green            5
                  custom           2
                  purple           1
                  red              1
buick enclave     white           69
                  NaN             42
                  black           30
                  silver          28
                  red             22
                  brown           21
                  grey            21
                  blue            21
                  custom          11
                  purple           4
                  green            2
cadillac escalade black          101
                  white           89
                  NaN             64
                  silver          22
                  grey            11
                  red              9
                  brown            9
                  custom           7
                  blue             6
                  green            4
chevrolet camaro  red             85
                  black           75
                  NaN             72
                  silver          48
                  white           37
                  grey            34
                  blue            21

We can see that while most models are missing quite a few color cells, similarly to the `cylinder` column, there tends to be one mode that stands out for each, so the missing values will be filled accordingly.

In [25]:
# Fill in the missing values in paint_color column by using the modes from model groups
df.loc[df['paint_color'].isna(), 'paint_color'] = (
    df.groupby('model')['paint_color'].transform(lambda color: color.mode().iloc[0])
)
df['paint_color'].value_counts(dropna=False)

paint_color
white     13835
black      9897
silver     7998
grey       5843
blue       4729
red        4705
green      1554
brown      1223
custom     1153
yellow      255
orange      231
purple      102
Name: count, dtype: int64

In [26]:
df.isna().sum()

price           0
model_year      0
model           0
condition       0
cylinders       0
fuel            0
odometer        0
transmission    0
type            0
paint_color     0
is_4wd          0
date_posted     0
days_listed     0
dtype: int64

***
#### `date_posted`

We will be converting `date_posted` to datetime for enrichment purposes.

In [27]:
df['date_posted'] = pd.to_datetime(df['date_posted'])
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   price         51525 non-null  int64         
 1   model_year    51525 non-null  int32         
 2   model         51525 non-null  object        
 3   condition     51525 non-null  object        
 4   cylinders     51525 non-null  int32         
 5   fuel          51525 non-null  object        
 6   odometer      51525 non-null  float64       
 7   transmission  51525 non-null  object        
 8   type          51525 non-null  object        
 9   paint_color   51525 non-null  object        
 10  is_4wd        51525 non-null  int32         
 11  date_posted   51525 non-null  datetime64[ns]
 12  days_listed   51525 non-null  int64         
dtypes: datetime64[ns](1), float64(1), int32(3), int64(2), object(6)
memory usage: 4.5+ MB


***
### `price`

In [28]:
df['price'].value_counts()

price
1        798
6995     719
5995     655
4995     624
3500     620
        ... 
58500      1
3993       1
32987      1
3744       1
7455       1
Name: count, Length: 3443, dtype: int64

We can see that $798$ vehicles have a price value of $1$.

In [29]:
low_price = df[df['price'] == 1]
low_price

price  model_year                  model  condition  cylinders    fuel  \
405        1        2014       chevrolet camaro  excellent          6     gas   
3063       1        1998    chevrolet silverado       good          8     gas   
3808       1        2007        chevrolet tahoe       good          8     gas   
3902       1        1996             ford f-150       fair          8     gas   
4140       1        2004    chevrolet silverado  excellent          8  diesel   
...      ...         ...                    ...        ...        ...     ...   
49699      1        2007  chevrolet trailblazer  excellent          8     gas   
49709      1        2013              ford f150  excellent          8     gas   
50245      1        1986    chevrolet silverado       good          8     gas   
50393      1        2003      gmc sierra 2500hd       good          8  diesel   
51256      1        2012         honda civic lx  excellent          4     gas   

       odometer transmission    type paint_color  is_4wd date_posted  \
405     71310.0    automatic   coupe         red       0  2018-07-14   
3063   164000.0    automatic  pickup       white       1  2018-10-11   
3808      200.0    automatic     SUV         red       0  2019-03-18   
3902   163000.0       manual   truck       white       0  2019-02-23   
4140    83000.0    automatic  pickup       white       1  2019-02-04   
...         ...          ...     ...         ...     ...         ...   
49699  104230.0    automatic     SUV       black       1  2018-08-06   
49709  139700.0        other  pickup         red       1  2019-03-11   
50245  129000.0    automatic   truck         red       1  2018-11-30   
50393  212300.0    automatic  pickup       black       1  2019-04-12   
51256   71262.0    automatic   sedan        blue       0  2018-05-06   

       days_listed  
405             29  
3063            49  
3808            63  
3902            54  
4140            14  
...            ...  
49699           28  
49709           18  
50245           50  
50393           28  
51256           53  

[798 rows x 13 columns]

We can see that the ads with this abnormality do not have many similarities other than being posted within 2 years of the data being collected, and even have a variety of `condition` values so we will leave the `price` values as is.

## Data Enhancement

We will now extract some data from certain columns in order to analyse our data further.

First we will extract the manufacturer data from the `model` column:

In [30]:
df['manufacturer'] = df['model'].str.split().str[0]
df['manufacturer'].value_counts()

manufacturer
ford             12672
chevrolet        10611
toyota            5445
honda             3485
ram               3316
jeep              3281
nissan            3208
gmc               2378
subaru            1272
dodge             1255
hyundai           1173
volkswagen         869
chrysler           838
kia                585
cadillac           322
buick              271
bmw                267
acura              236
mercedes-benz       41
Name: count, dtype: int64

Now we will extract `datetime` data from the `date_posted` column:

In [34]:
df['date_posted_year'] = df['date_posted'].dt.year
df['date_posted_month'] = df['date_posted'].dt.month_name()
df

price  model_year           model  condition  cylinders fuel  odometer  \
0       9400        2011          bmw x5       good          6  gas  145000.0   
1      25500        2013      ford f-150       good          6  gas   88705.0   
2       5500        2013  hyundai sonata   like new          4  gas  110000.0   
3       1500        2003      ford f-150       fair          8  gas  181613.0   
4      14900        2017    chrysler 200  excellent          4  gas   80903.0   
...      ...         ...             ...        ...        ...  ...       ...   
51520   9249        2013   nissan maxima   like new          6  gas   88136.0   
51521   2700        2002     honda civic    salvage          4  gas  181500.0   
51522   3950        2009  hyundai sonata  excellent          4  gas  128000.0   
51523   7455        2013  toyota corolla       good          4  gas  139573.0   
51524   6300        2014   nissan altima       good          4  gas  129000.0   

      transmission    type paint_color  is_4wd date_posted  days_listed  \
0        automatic     SUV       black       1  2018-06-23           19   
1        automatic  pickup       white       1  2018-10-19           50   
2        automatic   sedan         red       0  2019-02-07           79   
3        automatic  pickup       white       0  2019-03-22            9   
4        automatic   sedan       black       0  2019-04-02           28   
...            ...     ...         ...     ...         ...          ...   
51520    automatic   sedan       black       0  2018-10-03           37   
51521    automatic   sedan       white       0  2018-11-14           22   
51522    automatic   sedan        blue       0  2018-11-15           32   
51523    automatic   sedan       black       0  2018-07-02           71   
51524    automatic   sedan        grey       0  2018-06-05           10   

      manufacturer date_posted_month  date_posted_year  
0              bmw              June              2018  
1             ford           October              2018  
2          hyundai          February              2019  
3             ford             March              2019  
4         chrysler             April              2019  
...            ...               ...               ...  
51520       nissan           October              2018  
51521        honda          November              2018  
51522      hyundai          November              2018  
51523       toyota              July              2018  
51524       nissan              June              2018  

[51525 rows x 16 columns]

Now with those columns added we will add a `vehicle_age` column that contains the difference between the date the ad was posted and the model year of the vehicle:

In [35]:
df['vehicle_age'] = df['date_posted_year'] - df['model_year']
df.info()
df.to_csv('vehicles_us_fixed.csv')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 17 columns):
 #   Column             Non-Null Count  Dtype         
---  ------             --------------  -----         
 0   price              51525 non-null  int64         
 1   model_year         51525 non-null  int32         
 2   model              51525 non-null  object        
 3   condition          51525 non-null  object        
 4   cylinders          51525 non-null  int32         
 5   fuel               51525 non-null  object        
 6   odometer           51525 non-null  float64       
 7   transmission       51525 non-null  object        
 8   type               51525 non-null  object        
 9   paint_color        51525 non-null  object        
 10  is_4wd             51525 non-null  int32         
 11  date_posted        51525 non-null  datetime64[ns]
 12  days_listed        51525 non-null  int64         
 13  manufacturer       51525 non-null  object        
 14  date_p

## Visualizations

We will now make a few visualizations in order to make observations about our data, that will be used in our web app.

In [72]:
odometer_condition = px.scatter(df, x='vehicle_age', y='odometer', color='condition', title='Vehicle Condtion and Age', opacity=.7)
odometer_condition.show()

We can see that `vehicle_age` and `odometer` tends to affect what users put in the `condition` column, but some users mark vehicles with almost 1 million miles on the odometer as **like new** or **excellent**.

In [73]:
manufacturer_stats = px.histogram(df, title='Vehicle Types', x='type', color='manufacturer')
manufacturer_stats.show()

The most posted vehicle types are `SUV`, `Truck`, and then `sedan` which is to be expected as those are the most commonly used personal vehicles.

In [50]:
days = px.histogram(df, title='Histogram of Days listed', x='days_listed', color='condition')
days.show()

We can see from this that `condition` also doesn't affect how quickly a vehicle is sold on the site.

In [74]:
price = px.scatter(df, title='Price When Listed', x='date_posted', y='price', color='condition', opacity=.7)
price.show()

Most vehicles are priced under $60000$ with very few exceptions, with `fair` vehicles being the least expensive.